In [1]:
# Check Environment

import sys
print(sys.version)
print(sys.executable)

3.7.5 (default, Oct 31 2019, 15:18:51) [MSC v.1916 64 bit (AMD64)]
C:\Users\Dennis\anaconda3\envs\rc_env_np16p6\python.exe


In [2]:
# IMPORTS

import rescomp
import numpy as np

import pandas as pd

import plotly.express as px

# import matplotlib.pyplot as plt
# from mpl_toolkits import mplot3d

### Create Lorenz Dataset:

In [3]:
simulation_time_steps = 8000
dt = 2e-2

starting_point = np.array([-14.03020521, -20.88693127, 25.53545])
sim_data = rescomp.simulate_trajectory(
    sys_flag='lorenz', dt=dt, time_steps=simulation_time_steps,
    starting_point=starting_point)

### Create artificially "wrong" model and plot real and "fake" Lorenz Attractor:

In [17]:
#Create artificially "wrong" model by changing the system parameters:
eps1 = 0.0
eps2 = 0.1
eps3 = 0.0
model = lambda x: rescomp.simulations._normal_lorenz(x, sigma=10*(1+eps1), rho=28*(1+eps2), beta=8/3*(1+eps3))
model = lambda x: -x

# model_pred = lambda x: x + model(x)*dt
model_pred = lambda x: rescomp.simulations._runge_kutta(model, dt, x)

# test it:
x = np.zeros((simulation_time_steps, 3))

x[0] = starting_point
for i in range(1, simulation_time_steps):
    x_i = x[i-1]
    x[i] = model_pred(x_i)


# Plotly
sim_data_df = pd.DataFrame(data=sim_data, columns = ["x", "y", "z"])
sim_data_df["name"] = "true"
wrong_model_data_df = pd.DataFrame(data=x, columns = ["x", "y", "z"])
wrong_model_data_df["name"] = "wrong"
df = pd.concat([sim_data_df, wrong_model_data_df])
fig = px.line_3d(df, x = "x", y ="y", z="z", color = "name")
fig.show()


# Matplotlib: 
# fig = plt.figure(figsize=(6, 3), dpi=300)
# ax = fig.add_subplot(111, projection='3d')
# ax.plot(x[:, 0], x[:, 1], x[:, 2],
#         alpha=0.8, color='blue', linewidth = 0.1)
# ax.plot(sim_data[:, 0], sim_data[:, 1], sim_data[:, 2],
#         alpha=0.8, color='red', linewidth = 0.1)
# ax.set_title("Normal Lorenz63 System Simulated")
# ax.set_xlabel('x')
# ax.set_ylabel('y')
# ax.set_zlabel('z')
# plt.show()

### Create "normal" and different Hybrid Models:

In [18]:
n_dim = 1000

ESNs = {}

# The Baseline
np.random.seed(1)
name = "normal"
esn_normal = rescomp.esn.ESNWrapper()
esn_normal.create_network(n_dim = n_dim)
ESNs[name] = esn_normal

# Hybrid only at output: 
np.random.seed(1)
name = "hybrid out"
esn_hybrid_out = rescomp.esn.ESNHybrid()
esn_hybrid_out.create_network(n_dim = n_dim)
add_model_to_output = True
add_model_to_input = False
esn_hybrid_out.set_model(model_pred, add_model_to_input = add_model_to_input, add_model_to_output = add_model_to_output)
ESNs[name] = esn_hybrid_out

# Hybrid only at input:
np.random.seed(1)
name = "hybrid in"
esn_hybrid_in = rescomp.esn.ESNHybrid()
esn_hybrid_in.create_network(n_dim = n_dim)
add_model_to_output = False
add_model_to_input = True
gamma = 0.5
esn_hybrid_in.set_model(model_pred, add_model_to_input = add_model_to_input,
                        add_model_to_output = add_model_to_output,
                       gamma = gamma)
ESNs[name] = esn_hybrid_in

# Hybrid at in- and output: 
np.random.seed(1)
name = "hybrid both"
esn_hybrid_both = rescomp.esn.ESNHybrid()
esn_hybrid_both.create_network(n_dim = n_dim)
add_model_to_output = True
add_model_to_input = True
gamma = 0.5
esn_hybrid_both.set_model(model_pred, add_model_to_input = add_model_to_input,
                        add_model_to_output = add_model_to_output,
                       gamma = gamma)
ESNs[name] = esn_hybrid_both

### Train and predict:

In [19]:
train_sync_steps = 500
train_steps = 6000
pred_steps = 1500 

# For testing different W_in settings
w_in_sparse=True #True
w_in_ordered=True #False
w_in_no_update=False #False
act_fct_flag='tanh_simple' #'tanh_simple'
w_out_fit_flag="simple" #"simple"

ESNs_results = {}

for name, ESN in ESNs.items():
    print("---- Training and predicting " + name + " ----")
    ESNs_results[name] = ESN.train_and_predict(
        x_data=sim_data, train_sync_steps=train_sync_steps, train_steps=train_steps, 
        pred_steps=pred_steps, 
        w_in_sparse=w_in_sparse, w_in_ordered=w_in_ordered, w_in_no_update=w_in_no_update, act_fct_flag=act_fct_flag, 
        w_out_fit_flag=w_out_fit_flag
        )

---- Training and predicting normal ----
---- Training and predicting hybrid out ----
r_gen shape:  (5999, 1000)
u_train shape:  (5999, 3)
---- Training and predicting hybrid in ----
Actual percentage of Reservoir nodes connected to raw input:  50.0
xshape and model(x) shape:  (500, 3) (500, 3)
xshape after:  (500, 6)
win  shape:  (1000, 6)
xshape and model(x) shape:  (5999, 3) (5999, 3)
xshape after:  (5999, 6)
win  shape:  (1000, 6)
r_gen shape:  (5999, 1000)
---- Training and predicting hybrid both ----
Actual percentage of Reservoir nodes connected to raw input:  50.0
xshape and model(x) shape:  (500, 3) (500, 3)
xshape after:  (500, 6)
win  shape:  (1000, 6)
xshape and model(x) shape:  (5999, 3) (5999, 3)
xshape after:  (5999, 6)
win  shape:  (1000, 6)
r_gen shape:  (5999, 1000)
u_train shape:  (5999, 3)


### Create Dataframe used for plotting (plotly):

In [20]:
frames = []

get_test = True
for name, result in ESNs_results.items():
    y_pred, y_test = result
    
    if get_test:
        df_test = pd.DataFrame(data=y_test, columns = ["x", "y", "z"])
        df_test["name"] = "test"
        frames.append(df_test)
        get_test = False
    df_pred = pd.DataFrame(data=y_pred, columns = ["x", "y", "z"])
    df_pred["name"] = name + " pred"
    frames.append(df_pred)
        
df = pd.concat(frames)
print(df)

             x         y          z              name
0     1.955340  3.594315   9.957817              test
1     2.315795  4.292259   9.604431              test
2     2.750612  5.135080   9.337862              test
3     3.275032  6.149423   9.183554              test
4     3.906541  7.363522   9.178585              test
...        ...       ...        ...               ...
1495  0.187806 -2.673262  24.306688  hybrid both pred
1496 -0.325826 -2.627665  23.054479  hybrid both pred
1497 -0.743055 -2.637275  21.890930  hybrid both pred
1498 -1.091876 -2.706233  20.801383  hybrid both pred
1499 -1.396332 -2.844117  19.785490  hybrid both pred

[7500 rows x 4 columns]


### Plot x coordinate of models: prediction vs test:

In [21]:
fig = px.line(df, y="z", color='name')
fig.show()

### Plot attractor: 

In [22]:
fig = px.line_3d(df,x = "x", y ="y", z="z", color='name')
fig.show()

### Create Dataframe for RMSE:

In [10]:
frames = []

for name, result in ESNs_results.items():
    y_pred, y_test = result
    rmse = rescomp.measures.rmse_over_time(y_pred, y_test)
    df_rmse = pd.DataFrame(data=rmse, columns = ["rmse"])
    df_rmse["name"] = "rmse " + name
    frames.append(df_rmse)
        
df_rmse = pd.concat(frames)
print(df_rmse)

          rmse              name
0     0.001577       rmse normal
1     0.005005       rmse normal
2     0.010249       rmse normal
3     0.016799       rmse normal
4     0.022354       rmse normal
...        ...               ...
1495  2.550407  rmse hybrid both
1496  2.755714  rmse hybrid both
1497  3.042918  rmse hybrid both
1498  3.423090  rmse hybrid both
1499  3.907976  rmse hybrid both

[6000 rows x 2 columns]


### Plot RMSE:

In [11]:
fig = px.line(df_rmse, y="rmse", color='name')
fig.show()

-----------------------------------
# OLD

In [12]:
# print(esn_hybrid._w_out.shape)
# print(esn_normal._w_out.shape)

# print(np.average(esn_hybrid._w_out[:, -3:]))
# print(np.average(esn_hybrid._w_out[:, :-3]))

In [13]:
# fig1 = plt.figure(figsize=(9, 6), dpi=300)
# ax1 = fig1.add_subplot(111, projection='3d')

# ax1.plot(y_test_normal[:, 0], y_test_normal[:, 1], y_test_normal[:, 2],
#         alpha=0.8, color='blue', label='simulation')
# ax1.plot(y_pred_normal[:, 0], y_pred_normal[:, 1], y_pred_normal[:, 2],
#         alpha=0.8, color='orange', label='pred normal')
# ax1.plot(y_pred_hybrid[:, 0], y_pred_hybrid[:, 1], y_pred_hybrid[:, 2],
#         alpha=0.8, color='red', label='pred hybrid')

# start = y_test_normal[0]
# ax1.plot([start[0]], [start[1]], [start[2]], 
#          color='black', linestyle='', marker='o', label='starting point')

# ax1.set_title("Simulation vs Prediction")
# ax1.set_xlabel('x')
# ax1.set_ylabel('y')
# ax1.set_zlabel('z')
# plt.legend()
# plt.show()

In [14]:
# prediction_dict = {}

# y_test = None

# fig2 = plt.figure(figsize=(9, 6), dpi=300)
# ax2 = fig2.add_subplot(1, 1, 1)

# for name, prediction in prediction_dict.items():
#     rmse = rescomp.measures.rmse_over_time(time_series, y_test)
#     ax2.plot(rmse, linestyle='--', label=name)
#     print("AVG RMSE for " + name, np.average(rmse))

# ax2.set_title("RMSE")
# ax2.set_xlabel('time steps')
# ax2.set_ylabel('RMSE')
# plt.legend()
# plt.show()